<a href="https://colab.research.google.com/github/kentokura/python_medical_images/blob/master/chapter3/chap3_11.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import matplotlib.pyplot as plt
import numpy as np
import cv2
import pandas as pd
from google.colab.patches import cv2_imshow
from google.colab import drive
from IPython.display import Image, display_png

drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


## 3.11 画像の次元

- 1～3次元データを扱う


リスト 3.11.1 1次元配列から2次元配列作成する

In [4]:
row0 = [1, 2, 3]
row1 = [4, 5, 6]
row2 = [7, 8, 9]

d2_array = np.array([row0,row1,row2])
d1_array = d2_array.flatten() #ravenは破壊的なな変更
print("変換前：", d2_array.shape)
print("変換後：", d1_array.shape)

変換前： (3, 3)
変換後： (9,)


### 3.11.3 スタック画像

In [7]:
# スタックを読むこむ
import cv2

ret, images = cv2.imreadmulti('/content/drive/My Drive/DATASET/dataset/t1-head-8bit-64.tif')
stack = np.zeros((images[0].shape[0],images[0].shape[1],len(images)))
for i,img in enumerate(images):
  stack[:,:,i] = img
print(stack.shape)

(64, 64, 129)


In [8]:
#スライス送り
import plotly.graph_objects as go

nb_frames = 129

vol = stack
print(vol.shape)
vol = vol.T
r, c = images[0].shape # row,col

# set frames
fig = go.Figure(frames=[go.Frame(data=go.Surface(z=((nb_frames-1)*0.1 - k * 0.1) * np.ones((r, c)),
                                                 surfacecolor=np.flipud(vol[k]),
                                                 cmin=0, cmax=255),name=str(k)
                                 ) for k in range(nb_frames)])

# Add data to be displayed before animation starts
fig.add_trace(go.Surface(
    z=(nb_frames-1)*0.1 * np.ones((r, c)),
    surfacecolor=np.flipud(vol[0]),
    colorscale='Gray',
    cmin=0, cmax=200,
    colorbar=dict(thickness=20, ticklen=4)
    ))


def frame_args(duration):
    return {
            "frame": {"duration": duration},
            "mode": "immediate",
            "fromcurrent": True,
            "transition": {"duration": duration, "easing": "linear"},
        }

sliders = [
            {
                "pad": {"b": 10, "t": 60},
                "len": 0.9,
                "x": 0.1,
                "y": 0,
                "steps": [
                    {
                        "args": [[f.name], frame_args(0)],
                        "label": str(k),
                        "method": "animate",
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]

# Layout
fig.update_layout(
         title='Slices in volumetric data',
         width=600,
         height=600,
         scene=dict(
                    zaxis=dict(range=[-0.1, (nb_frames)*0.1], autorange=False),
                    aspectratio=dict(x=1, y=1, z=1),
                    ),
         updatemenus = [
            {
                "buttons": [
                    {
                        "args": [None, frame_args(100)],
                        "label": "&#9654;", # play symbol
                        "method": "animate",
                    },
                    {
                        "args": [[None], frame_args(0)],
                        "label": "&#9724;", # pause symbol
                        "method": "animate",
                    },
                ],
                "direction": "left",
                "pad": {"r": 10, "t": 70},
                "type": "buttons",
                "x": 0.1,
                "y": 0,
            }
         ],
         sliders=sliders
)

fig.show()

(64, 64, 129)
